Importando librerias

In [ ]:
import pandas as pd
import requests
from bs4 import BeautifulSoup
from pprint import pprint
from datetime import datetime
from IPython.display import HTML, display
import folium
import json
import re
import random
import sqlite3
import os
from geopy.geocoders import Nominatim
from geopy.exc import GeocoderTimedOut, GeocoderServiceError
import time


Configuraciones de visualización del dataframe con Pandas

In [ ]:
# Para imprimir toda a informacción de celdas muy largas
pd.set_option('display.max_columns', 500)

# Para imprimir todas las líneas de un dataframe
pd.set_option('display.max_rows', None)

# Para mostrar el ancho máximo de las columnas
pd.set_option('display.max_colwidth', 500)

----------------------------------------

extracción datos de meteo

In [ ]:
API_KEY = ''
city = "Madrid"
url = f"http://api.weatherapi.com/v1/forecast.json?key={API_KEY}&q={city}&days=7&aqi=no&alerts=no&lang=es"

response = requests.get(url)
data = response.json()

for day in data['forecast']['forecastday']:
    date = day['date']
    avg_temp = day['day']['avgtemp_c']
    condition = day['day']['condition']['text']
    will_rain = "rain" in condition.lower()

    print(f"📅 {date}")
    print(f"   🌡️ Temperatura media: {avg_temp}°C")
    print(f"   🌥️ Predicción: {condition}")
    print(f"   ☔ ¿LLoverá? {'Si' if will_rain else 'No'}\n")


------------------------------------------------

Scrapeando datos parques

In [8]:
url = "https://www.pa-community.com/parques"
get_req = requests.get(url)
soup = BeautifulSoup(get_req.text, "html.parser")

In [9]:
soup

<!DOCTYPE html>

<html>
<head>
<!-- Google Tag Manager -->
<script>!function(){"use strict";function l(e){for(var t=e,r=0,n=document.cookie.split(";");r<n.length;r++){var o=n[r].split("=");if(o[0].trim()===t)return o[1]}}function s(e){return localStorage.getItem(e)}function u(e){return window[e]}function d(e,t){e=document.querySelector(e);return t?null==e?void 0:e.getAttribute(t):null==e?void 0:e.textContent}var e=window,t=document,r="script",n="dataLayer",o="KZL3JD",a="https://sgtm.pa-community.com",i="https://load.sgtm.pa-community.com",c="lavpljnj",E="stapeUserId",I="",v="",g=!1;try{var g=!!E&&(m=navigator.userAgent,!!(m=new RegExp("Version/([0-9._]+)(.*Mobile)?.*Safari.*").exec(m)))&&16.4<=parseFloat(m[1]),A="stapeUserId"===E,f=g&&!A?function(e,t,r){void 0===t&&(t="");var n={cookie:l,localStorage:s,jsVariable:u,cssSelector:d},t=Array.isArray(t)?t:[t];if(e&&n[e])for(var o=n[e],a=0,i=t;a<i.length;a++){var c=i[a],c=r?o(c,r):o(c);if(c)return c}else console.warn("invalid uid source",e)}

In [15]:
from bs4 import BeautifulSoup

parques_espana = []

# Encuentra todos los elementos 'li' que contienen la información del parque
park_items = soup.find_all('li', class_='cat-')

for item in park_items:
    # Dentro de cada 'li', busca el div con la clase 'card-park'
    card_park = item.find('div', class_='card-park')
    if card_park:
        # Busca el elemento 'h3' que contiene el nombre del parque
        h3_tag = card_park.find('h3')
        if h3_tag:
            nombre_parque = h3_tag.find('a').text
            # Busca el elemento 'p' que contiene la ubicación del parque
            ubicacion_tag = card_park.find('div').find('p')
            if ubicacion_tag:
                ubicacion = ubicacion_tag.contents[0].strip()
                # Verifica si el parque está en España
                if "España" in ubicacion:
                    # Añadimos solo el nombre del parque a la lista
                    parques_espana.append(nombre_parque)

print(parques_espana)

['DinoPark Algar', 'Aqualava', 'Acuario de Sevilla', 'Oasis Wildlife', 'Loro Parque', 'Siam Park', 'Bioparc Valencia', 'Mundomar', 'Jungle Park', 'Ciudad de las Artes y las Ciencias', 'Palma Aquarium', 'Aquarium Costa de Almería', 'Oceanografic', 'Acuario Poema del Mar', 'Western Water Park Magaluf', 'Parque de la Naturaleza de Cabárceno', 'Puy du Fou Toledo', 'Acuario de Gijón Bioparc', 'Acuario de Zaragoza', 'Water World', "Aquadiver Platja d'Aro", 'Aqualand Costa Adeje', 'Aqualandia', 'Macabre Scream Park', 'Bioparc Fuengirola', 'Sendaviva', 'Aquarium Donostia', 'Dinópolis Teruel', 'Palmitos Park', 'Lacuniacha', 'Marineland Catalunya', 'Atlantis Aquarium Madrid', 'AquaTropic', 'Aqualand Maspalomas', 'Zoo de Madrid', 'Parque Warner Madrid', 'Isla Mágica', 'PortAventura', 'Aquópolis Costa Daurada', 'Katmandu Park Magaluf', 'Oasys MiniHollywood', 'Holiday World Maspalomas', 'Aquavera', 'Terra Natura Murcia', 'Faunia', 'PortAventura Caribe Aquatic Park', 'Selwo Marina', 'Parque de Atrac

In [18]:
from bs4 import BeautifulSoup
from geopy.geocoders import Nominatim
from geopy.exc import GeocoderTimedOut, GeocoderServiceError


parques_coordenadas = {}
geolocator = Nominatim(user_agent="parques_app") # Reemplaza "parques_app" con un nombre único para tu aplicación

def geolocalizar(nombre_parque, ubicacion):
    """Intenta geolocalizar un parque."""
    direccion = f"{nombre_parque}, {ubicacion}"
    try:
        location = geolocator.geocode(direccion, timeout=10)
        if location:
            return location.latitude, location.longitude
        else:
            direccion_alternativa = f"{nombre_parque}, España"
            location_alternativo = geolocator.geocode(direccion_alternativa, timeout=10)
            if location_alternativo:
                return location_alternativo.latitude, location_alternativo.longitude
            else:
                print(f"No se pudieron encontrar coordenadas para: {nombre_parque}, {ubicacion}")
                return None, None
    except GeocoderTimedOut:
        print(f"Tiempo de espera agotado para: {nombre_parque}, {ubicacion}")
        return geolocalizar(nombre_parque, ubicacion) # Reintentar
    except GeocoderServiceError as e:
        print(f"Error del servicio de geocodificación para {nombre_parque}: {e}")
        return None, None

# Encuentra todos los elementos 'li' que contienen la información del parque
park_items = soup.find_all('li', class_='cat-')

for item in park_items:
    # Dentro de cada 'li', busca el div con la clase 'card-park'
    card_park = item.find('div', class_='card-park')
    if card_park:
        # Busca el elemento 'h3' que contiene el nombre del parque
        h3_tag = card_park.find('h3')
        if h3_tag:
            nombre_parque = h3_tag.find('a').text
            # Busca el elemento 'p' que contiene la ubicación del parque
            ubicacion_tag = card_park.find('div').find('p')
            if ubicacion_tag:
                ubicacion = ubicacion_tag.contents[0].strip()
                # Verifica si el parque está en España
                if "España" in ubicacion:
                    latitud, longitud = geolocalizar(nombre_parque, ubicacion)
                    if latitud is not None and longitud is not None:
                        parques_coordenadas[nombre_parque] = {"latitud": latitud, "longitud": longitud}

print(parques_coordenadas)

No se pudieron encontrar coordenadas para: Western Water Park Magaluf, España ·
No se pudieron encontrar coordenadas para: Acuario de Gijón Bioparc, España ·
No se pudieron encontrar coordenadas para: Macabre Scream Park, España ·
No se pudieron encontrar coordenadas para: Katmandu Park Magaluf, España ·
No se pudieron encontrar coordenadas para: Holiday World Maspalomas, España ·
No se pudieron encontrar coordenadas para: Guadalpark Sevilla (Aquópolis), España ·
No se pudieron encontrar coordenadas para: Aquarium de Barcelona, España ·
No se pudieron encontrar coordenadas para: Ferrari Land PortAventura, España ·
No se pudieron encontrar coordenadas para: Aqua Natura Murcia, España ·
No se pudieron encontrar coordenadas para: Mortenostrum Scream Park, España ·
No se pudieron encontrar coordenadas para: Aqua Park Costa Teguise, España ·
{'DinoPark Algar': {'latitud': 38.651412, 'longitud': -0.0903111}, 'Aqualava': {'latitud': 28.8630834, 'longitud': -13.8429163}, 'Acuario de Sevilla': 

Creando lista de diccionarios con informaciones de los parques

In [11]:
parks_info_list = [
    {
        "name": "DinoPark Algar",
        "url": "https://www.dinopark.es/",
        "longitude": -0.1123,
        "latitude": 38.6486,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Aqualava",
        "url": "https://www.aqualava.net/",
        "longitude": -13.8321,
        "latitude": 28.8636,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Acuario de Sevilla",
        "url": "https://www.acuariosevilla.es/",
        "longitude": -5.9869,
        "latitude": 37.3764,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Oasis Wildlife",
        "url": "https://www.oasiswildlifefuerteventura.com/",
        "longitude": -14.1611,
        "latitude": 28.2083,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Loro Parque",
        "url": "https://www.loroparque.com/",
        "longitude": -16.5480,
        "latitude": 28.4058,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Siam Park",
        "url": "https://www.siampark.net/",
        "longitude": -16.7265,
        "latitude": 28.0718,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Bioparc Valencia",
        "url": "https://www.bioparcvalencia.es/",
        "longitude": -0.4077,
        "latitude": 39.4789,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Mundomar",
        "url": "https://www.mundomar.es/",
        "longitude": -0.1064,
        "latitude": 38.5406,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Jungle Park",
        "url": "https://www.aguilasjunglepark.com/",
        "longitude": -16.6825,
        "latitude": 28.0790,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Ciudad de las Artes y las Ciencias",
        "url": "https://www.cac.es/",
        "longitude": -0.3530,
        "latitude": 39.4550,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Palma Aquarium",
        "url": "https://www.palmaaquarium.com/",
        "longitude": 2.7380,
        "latitude": 39.5250,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Aquarium Costa de Almería",
        "url": "https://www.aquariumcostadealmeria.com/",
        "longitude": -2.6140,
        "latitude": 36.7650,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Oceanogràfic",
        "url": "https://www.oceanografic.org/",
        "longitude": -0.3517,
        "latitude": 39.4541,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Acuario Poema del Mar",
        "url": "https://www.poema-del-mar.com/",
        "longitude": -15.4236,
        "latitude": 28.1426,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Western Water Park Magaluf",
        "url": "https://www.westernpark.com/",
        "longitude": 2.5350,
        "latitude": 39.5080,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Parque de la Naturaleza de Cabárceno",
        "url": "https://www.parquedecabarceno.com/",
        "longitude": -3.8297,
        "latitude": 43.3467,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Puy du Fou Toledo",
        "url": "https://www.puydufou.com/espana/",
        "longitude": -4.0500,
        "latitude": 39.8910,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Acuario de Gijón Bioparc",
        "url": "https://www.acuariodegijon.es/",
        "longitude": -5.6330,
        "latitude": 43.5350,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Acuario de Zaragoza",
        "url": "https://www.acuariodezaragoza.com/",
        "longitude": -0.8990,
        "latitude": 41.6600,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Water World",
        "url": "https://www.waterworld.es/",
        "longitude": 2.8250,
        "latitude": 41.6980,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Aquadiver Platja d'Aro",
        "url": "https://www.aquadiver.com/",
        "longitude": 3.0639,
        "latitude": 41.8256,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Aqualand Costa Adeje",
        "url": "https://www.aqualand.es/costa-adeje/",
        "longitude": -16.7278,
        "latitude": 28.0802,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Aqualandia",
        "url": "https://www.aqualandia.net/",
        "longitude": -0.1100,
        "latitude": 38.5400,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Macabre Scream Park",
        "url": "https://www.macabrescreampark.com/",
        "longitude": -0.3763,
        "latitude": 39.4699,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Bioparc Fuengirola",
        "url": "https://www.bioparcfuengirola.es/",
        "longitude": -4.6240,
        "latitude": 36.5410,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Sendaviva",
        "url": "https://www.sendaviva.com/",
        "longitude": -1.5980,
        "latitude": 42.1760,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Aquarium Donostia",
        "url": "https://www.aquariumss.com/",
        "longitude": -1.9860,
        "latitude": 43.3240,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Dinópolis Teruel",
        "url": "https://www.dinopolis.com/",
        "longitude": -1.1060,
        "latitude": 40.3300,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Palmitos Park",
        "url": "https://www.palmitospark.es/",
        "longitude": -15.6012,
        "latitude": 27.7876,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Lacuniacha",
        "url": "https://www.lacuniacha.es/",
        "longitude": -0.3330,
        "latitude": 42.6670,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Marineland Catalunya",
        "url": "https://www.marineland.es/",
        "longitude": 2.7534,
        "latitude": 41.6608,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Atlantis Aquarium Madrid",
        "url": "https://www.atlantisaquarium.com/",
        "longitude": -3.8190,
        "latitude": 40.3720,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "AquaTropic",
        "url": "https://www.aquatropic.com/",
        "longitude": -3.7000,
        "latitude": 36.7320,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Aqualand Maspalomas",
        "url": "https://www.aqualand.es/maspalomas/",
        "longitude": -15.5930,
        "latitude": 27.7700,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Zoo de Madrid",
        "url": "https://www.zoomadrid.com/",
        "longitude": -3.7619,
        "latitude": 40.4036,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Parque Warner Madrid",
        "url": "https://www.parquewarner.com/",
        "longitude": -3.5943,
        "latitude": 40.2317,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Isla Mágica",
        "url": "https://www.islamagica.es/",
        "longitude": -6.0020,
        "latitude": 37.3970,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "PortAventura",
        "url": "https://www.portaventuraworld.com/",
        "longitude": 1.1540,
        "latitude": 41.0870,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Aquópolis Costa Daurada",
        "url": "https://www.aquopolis.es/costa-daurada/",
        "longitude": 1.1800,
        "latitude": 41.0800,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Katmandu Park Magaluf",
        "url": "https://www.katmandupark.com/",
        "longitude": 2.5380,
        "latitude": 39.5100,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Oasys MiniHollywood",
        "url": "https://www.oasysparquetematico.com/",
        "longitude": -2.4330,
        "latitude": 37.0010,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Holiday World Maspalomas",
        "url": "https://www.holidayworldmaspalomas.com/",
        "longitude": -15.5820,
        "latitude": 27.7740,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Aquavera",
        "url": "https://www.aquavera.com/",
        "longitude": -1.8230,
        "latitude": 37.2340,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Terra Natura Murcia",
        "url": "https://www.terranatura.com/",
        "longitude": -1.1660,
        "latitude": 38.0160,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Faunia",
        "url": "https://www.faunia.es/",
        "longitude": -3.6270,
        "latitude": 40.4000,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "PortAventura Caribe Aquatic Park",
        "url": "https://www.portaventuraworld.com/parques/caribe-aquatic-park",
        "longitude": 1.1500,
        "latitude": 41.0880,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Selwo Marina",
        "url": "https://www.selwomarina.es/",
        "longitude": -4.5250,
        "latitude": 36.5960,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Parque de Atracciones Madrid",
        "url": "https://www.parquedeatracciones.es/",
        "longitude": -3.7312,
        "latitude": 40.4091,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Aquópolis Torrevieja",
        "url": "https://www.aquopolis.es/torrevieja/",
        "longitude": -0.6870,
        "latitude": 37.9930,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Terra Natura Benidorm",
        "url": "https://www.terranatura.com/",
        "longitude": -0.4920,
        "latitude": 38.5670,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Aquópolis Villanueva de la Cañada",
        "url": "https://www.aquopolis.es/madrid/",
        "longitude": -3.9991,
        "latitude": 40.4474,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Illa Fantasia",
        "url": "https://www.illafantasia.com/",
        "longitude": 2.3339,
        "latitude": 41.5097,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Tibidabo",
        "url": "https://www.tibidabo.cat/",
        "longitude": 2.1185,
        "latitude": 41.4225,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Selwo Aventura",
        "url": "https://www.selwo.es/",
        "longitude": -5.0492,
        "latitude": 36.4896,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Aqualand Torremolinos",
        "url": "https://www.aqualand.es/torremolinos/",
        "longitude": -4.5097,
        "latitude": 36.6261,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Guadalpark Sevilla (Aquópolis)",
        "url": "https://www.aquopolis.es/sevilla/",
        "longitude": -5.9304,
        "latitude": 37.3891,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Aqua Natura Benidorm",
        "url": "https://benidorm.terranatura.com/aqua-natura/",
        "longitude": -0.4918,
        "latitude": 38.5671,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Aqualand Bahía de Cádiz",
        "url": "https://www.aqualand.es/bahiadecadiz/",
        "longitude": -6.2584,
        "latitude": 36.5158,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Aquópolis Cullera",
        "url": "https://www.aquopolis.es/cullera/",
        "longitude": -0.2483,
        "latitude": 39.1645,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Sea Life Benalmádena (Málaga)",
        "url": "https://www.visitsealife.com/benalmadena/",
        "longitude": -4.5173,
        "latitude": 36.5954,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Aquavelis",
        "url": "https://www.aquavelis.es/",
        "longitude": -4.0935,
        "latitude": 36.7434,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Agua Mágica",
        "url": "https://www.islamagica.es/agua-magica/",
        "longitude": -6.0015,
        "latitude": 37.3969,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Mario Park",
        "url": "https://www.mariopark.com/",
        "longitude": -2.4512,
        "latitude": 36.8258,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Pola Park",
        "url": "https://www.polapark.com/",
        "longitude": -0.5531,
        "latitude": 38.1910,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Parque de Atracciones de Zaragoza",
        "url": "https://www.atraczaragoza.com/",
        "longitude": -0.9278,
        "latitude": 41.6348,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Zoo de Barcelona",
        "url": "https://www.zoobarcelona.cat/",
        "longitude": 2.1925,
        "latitude": 41.3884,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Terra Mítica",
        "url": "https://www.terramiticapark.com/",
        "longitude": -0.1468,
        "latitude": 38.5636,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Aquópolis Cartaya",
        "url": "https://www.aquopolis.es/cartaya/",
        "longitude": -7.0052,
        "latitude": 37.2775,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Aquarium de Barcelona",
        "url": "https://www.aquariumbcn.com/",
        "longitude": 2.1850,
        "latitude": 41.3761,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Ferrari Land PortAventura",
        "url": "https://www.portaventuraworld.com/parques/ferrari-land",
        "longitude": 1.1523,
        "latitude": 41.0875,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Aqualeón",
        "url": "https://www.aqualeon.es/",
        "longitude": 1.5265,
        "latitude": 41.2445,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Aqualand el Arenal",
        "url": "https://www.aqualand.es/elarenal/",
        "longitude": 2.7380,
        "latitude": 39.5082,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Warner Beach",
        "url": "https://www.parquewarnerbeach.com/",
        "longitude": -3.5917,
        "latitude": 40.2307,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Aqua Natura Murcia",
        "url": "https://murcia.terranatura.com/aqua-natura/",
        "longitude": -1.1681,
        "latitude": 38.0157,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Mortenostrum Scream Park",
        "url": "https://mortenostrum.com/",
        "longitude": -0.4062,
        "latitude": 39.4982,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Crocodile Park",
        "url": "https://www.cocodrilospark.com/",
        "longitude": -4.5106,
        "latitude": 36.6218,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Aquarock Menorca",
        "url": "https://www.aquarock-menorca.com/",
        "longitude": 3.8408,
        "latitude": 39.9893,
        "tags": "ocio",
        "data_source":"parks_list"
    },
    {
        "name": "Aqua Park Costa Teguise",
        "url": "https://aquaparklanzarote.es/",
        "longitude": -13.5140,
        "latitude": 28.9983,
        "tags": "ocio",
        "data_source":"parks_list"
    }
]


Prueba de visualización de los parques en un mapa

In [ ]:
map = folium.Map(location=[40.0, -3.5], zoom_start=6)

# Añadir marcadores para cada parque
for park in parks_info_list:
    popup_html = f"<b>{park['name']}</b><br><a href='{park['url']}' target='_blank'>Website</a>"
    folium.Marker(
        location=[park["latitude"], park["longitude"]],
        popup=popup_html,
        icon=folium.Icon(color="blue", icon="info-sign")
    ).add_to(map)

In [13]:
map

agregando ID a cada parque, creando id's que comienzan en 0 y que contienen 12 dígitos para diferenciarlo de los demás eventos extraídos de otras fuentes

In [14]:
park_list_df = pd.DataFrame(parks_info_list)

In [ ]:
# Generar una secuencia de ID con ceros a la izquierda
num_parks = len(park_list_df)
ids = [f"{i+1:012d}" for i in range(num_parks)]

# Insertar la columna 'ID' al comienzo del DataFrame
park_list_df.insert(0, 'event_id', ids)

In [ ]:
park_list_df.head() 

event_id                name  \
0  000000000001      DinoPark Algar   
1  000000000002            Aqualava   
2  000000000003  Acuario de Sevilla   
3  000000000004      Oasis Wildlife   
4  000000000005         Loro Parque   

                                           url  longitude  latitude  tags  \
0                     https://www.dinopark.es/    -0.1123   38.6486  ocio   
1                    https://www.aqualava.net/   -13.8321   28.8636  ocio   
2               https://www.acuariosevilla.es/    -5.9869   37.3764  ocio   
3  https://www.oasiswildlifefuerteventura.com/   -14.1611   28.2083  ocio   
4                  https://www.loroparque.com/   -16.5480   28.4058  ocio   

  data_source  
0  parks_list  
1  parks_list  
2  parks_list  
3  parks_list  
4  parks_list

In [ ]:
# Cargando variable de entorno

RENDER_DB_URI = os.getenv("RENDER_DB_URI")
TABLE_NAME = 'all_events'
UNIQUE_ID_COLUMN = 'event_id'

# Columnas existentes en la tabla eventos en la base de datos
db_columns = [
    'min_age', 'max_age', 'url', 'start_time', 'start_date', 'end_time',
    'end_date', 'duration', 'venue_name', 'venue_address', 'event_id',
    'latitude', 'summary', 'is_online_event', 'tickets_url', 'tags',
    'data_source', 'image', 'age_range', 'longitude', 'name'
]

# Columnas del dataframe
df_columns = park_list_df.columns.tolist()

# Identificar columnas faltantes en el DataFrame
missing_columns = [col for col in db_columns if col not in df_columns]

# Agregar columnas faltantes al DataFrame con valores nulos
for col in missing_columns:
    park_list_df[col] = None

# Renombrar las columnas del DataFrame para que coincidan con las columnas de la base de datos cuando sea necesario
# Suponiendo que 'ID' en el DataFrame debe corresponder a 'event_id' en la base de datos
# park_list_df = park_list_df.rename(columns={'ID': 'event_id'})

# Selecionar sólo las columnas que existen en la tabla de la base de datos, en el orden correcto
park_list_df_for_db = park_list_df[db_columns]

# Creando motor SQLAlchemy
engine = create_engine(RENDER_DB_URI)

try:
    # Establecer una conexión a la base de datos
    with engine.connect() as connection:
        # Insertar el DataFrame en la base de datos
        park_list_df_for_db.to_sql(
            TABLE_NAME,
            con=connection,
            if_exists='append',  # O 'reemplazar'/'fallar' según tus necesidades
            index=False
        )
        print(f"Data from 'park_list_df' successfully inserted into '{TABLE_NAME}'.")

except Exception as e:
    print(f"An error occurred during database insertion: {e}")
finally:
    # Dispose of the engine
    engine.dispose()

An error occurred during database insertion: (psycopg2.errors.UniqueViolation) duplicate key value violates unique constraint "all_events_pkey"
DETAIL:  Key (event_id)=(000000000001) already exists.

[SQL: INSERT INTO all_events (min_age, max_age, url, start_time, start_date, end_time, end_date, duration, venue_name, venue_address, event_id, latitude, summary, is_online_event, tickets_url, tags, data_source, image, age_range, longitude, name) VALUES (% ... 29872 characters truncated ... (tags__77)s, %(data_source__77)s, %(image__77)s, %(age_range__77)s, %(longitude__77)s, %(name__77)s)]
[parameters: {'end_date__0': None, 'name__0': 'DinoPark Algar', 'age_range__0': None, 'start_time__0': None, 'start_date__0': None, 'duration__0': None, 'tags__0': 'ocio', 'event_id__0': '000000000001', 'longitude__0': -0.1123, 'tickets_url__0': None, 'url__0': 'https://www.dinopark.es/', 'is_online_event__0': None, 'end_time__0': None, 'data_source__0': 'parks_list', 'max_age__0': None, 'venue_name__0'

-------------------------------------------------

Recopilación de datos sobre cines

In [52]:
url = "https://www.sensacine.com/cines/provincias-27410/"
get_req = requests.get(url)
soup = BeautifulSoup(get_req.text, "html.parser")

In [104]:
# import requests
# from bs4 import BeautifulSoup

# base_url = "https://www.sensacine.com"
# start_url = base_url + "/cines/"
# province_urls = []

# try:
#     response = requests.get(start_url)
#     response.raise_for_status()
#     soup = BeautifulSoup(response.content, 'html.parser')

#     province_link_elements = soup.select('.mdl-more-item')

#     for link_tag in province_link_elements:
#         href = link_tag.get('href')
#         if href:
#             full_province_url = base_url + href
#             province_urls.append(full_province_url)
#             print(f"Found province URL: {full_province_url}")

#     del province_urls[0:21]
#     print("\nList of all province URLs:")
#     for url in province_urls:
#         print(url)

# except requests.exceptions.RequestException as e:
#     print(f"Error fetching {start_url}: {e}")
# except Exception as e:
#     print(f"An error occurred: {e}")

In [ ]:
import requests
from bs4 import BeautifulSoup
import json

base_url = "https://www.sensacine.com"
start_url = base_url + "/cines/"
province_urls = []
all_cinema_data = {}

def extract_cinema_data(soup, province_url):
    cinema_data = []
    cinema_info_elements = soup.select('.theater-card') # Ajustar si es necesario

    for cinema_card in cinema_info_elements:
        name_element = cinema_card.select_one('span.add-theater-anchor[data-theater]')
        address_element = cinema_card.select_one('address.address')

        if name_element and address_element:
            data_theater_str = name_element.get('data-theater')
            try:
                data_theater = json.loads(data_theater_str)
                cinema_name = data_theater.get('name')
                cinema_address = address_element.text.strip()
                cinema_data.append({'name': cinema_name, 'address': cinema_address})
            except json.JSONDecodeError:
                print(f"Error decoding JSON for cinema name on {province_url}")
    return cinema_data

try:
    # obtener la página inicial para obtener los enlaces de las provincias
    response = requests.get(start_url)
    response.raise_for_status()
    soup_initial = BeautifulSoup(response.content, 'html.parser')

    province_link_elements = soup_initial.select('.mdl-more-item')

    for link_tag in province_link_elements:
        href = link_tag.get('href')
        if href:
            full_province_url = base_url + href
            province_urls.append(full_province_url)
            print(f"Found province URL: {full_province_url}")

    del province_urls[0:21] # Mantenga esta línea para filtrar las URL

# Iterar a través de cada URL de provincia y manejar la paginación
    for province_url in province_urls:
        print(f"\n--- Scraping cinemas in: {province_url} ---")
        all_cinemas_in_province = []
        current_page_url = province_url
        page_number = 1
        all_visited_pages = [{'url': current_page_url}]

        page_urls_to_visit = [province_url]
        visited_urls = set()

        # En la primera página, obtener previamente todas las URL de la página desde la paginación
        try:
            response_province = requests.get(province_url)
            response_province.raise_for_status()
            province_soup = BeautifulSoup(response_province.content, 'html.parser')

            # Extraer datos de la primera página
            cinemas_on_page = extract_cinema_data(province_soup, province_url)
            all_cinemas_in_province.extend(cinemas_on_page)
            visited_urls.add(province_url)

            # Obtener enlaces de paginación
            pagination_links = province_soup.select('nav.pagination.cf div.pagination-item-holder a.button.item[href]')
            for link in pagination_links:
                href = link.get('href')
                full_url = base_url + href
                if full_url not in visited_urls and full_url not in page_urls_to_visit:
                    page_urls_to_visit.append(full_url)

        except Exception as e:
            print(f"Error processing first page of {province_url}: {e}")

        # Visita las páginas restantes (2, 3, etc.)
        for page_url in page_urls_to_visit[1:]:  # Salta el primero, ya está hecho
            print(f"  - Scraping additional page: {page_url}")
            try:
                response = requests.get(page_url)
                response.raise_for_status()
                soup = BeautifulSoup(response.content, 'html.parser')

                cinemas_on_page = extract_cinema_data(soup, page_url)
                all_cinemas_in_province.extend(cinemas_on_page)
                visited_urls.add(page_url)

            except Exception as e:
                print(f"Error processing {page_url}: {e}")

        # Extraer el nombre de la provincia de la URL inicial
        province_name = province_url.split('/')[-2].split('-')[-1].capitalize()
        all_cinema_data[province_name] = all_cinemas_in_province # Almacenar la lista acumulada

    # Generar los datos recopilados como JSON
    print("\n--- Collected Cinema Data (with Pagination) ---")
    print(json.dumps(all_cinema_data, indent=4, ensure_ascii=False))

except requests.exceptions.RequestException as e:
    print(f"Error fetching {start_url}: {e}")
except Exception as e:
    print(f"An error occurred: {e}")

Found province URL: https://www.sensacine.com/cines/ciudades-72730/
Found province URL: https://www.sensacine.com/cines/ciudades-72386/
Found province URL: https://www.sensacine.com/cines/ciudades-72413/
Found province URL: https://www.sensacine.com/cines/ciudades-50788/
Found province URL: https://www.sensacine.com/cines/ciudades-72480/
Found province URL: https://www.sensacine.com/cines/ciudades-72170/
Found province URL: https://www.sensacine.com/cines/ciudades-72234/
Found province URL: https://www.sensacine.com/cines/ciudades-72640/
Found province URL: https://www.sensacine.com/cines/ciudades-72255/
Found province URL: https://www.sensacine.com/cines/ciudades-72166/
Found province URL: https://www.sensacine.com/cines/ciudades-72368/
Found province URL: https://www.sensacine.com/cines/ciudades-72703/
Found province URL: https://www.sensacine.com/cines/ciudades-72335/
Found province URL: https://www.sensacine.com/cines/ciudades-72684/
Found province URL: https://www.sensacine.com/ci

In [87]:
all_cinema_data

{'27438': [{'name': 'Cinesa Marineda City',
   'address': 'Centro comercial Marineda City\nAvenida Arteixo 43 15008 A Coruña'},
  {'name': 'Cantones Cines',
   'address': 'Los Cantones Village - Avda. Alférez Provisional, 3 15003 A Coruña'},
  {'name': 'Yelmo Cines Espacio Coruña',
   'address': 'Centro Comercial Espacio Coruña Parcela PIII 17 - Sector S-7 Recinto Ferial - Lu 15008 A Coruña'},
  {'name': 'Cines Forum Metropolitano',
   'address': 'Calle Río Monelos, 1 15006 A Coruña'},
  {'name': 'Cinesa As Cancelas',
   'address': 'Centro Comercial As Cancelas\nAvenida Do Camiño Francés 3 15703 Santiago De Compostela'},
  {'name': 'Multicines Compostela',
   'address': 'Rua Ramón Piñeiro, nº 2 15702 Santiago De Compostela'},
  {'name': 'Numax',
   'address': 'Rúa de Concepción Arenal, 9 15702 Santiago De Compostela'},
  {'name': 'Cine Duplex', 'address': 'Travesía de Moreno, 18 15403 Ferrol'},
  {'name': 'Cines Xunqueira', 'address': 'Relleno De , s/n 15270 Cee'},
  {'name': 'Barbanza

In [88]:
all_cinemas = []
for province_data in all_cinema_data.values():
    all_cinemas.extend(province_data)

all_cinemas_df = pd.DataFrame(all_cinemas)

In [89]:
all_cinemas_df

name  \
0          Cinesa Marineda City   
1                Cantones Cines   
2    Yelmo Cines Espacio Coruña   
3     Cines Forum Metropolitano   
4            Cinesa As Cancelas   
..                          ...   
596         Cine Sala Cervantes   
597              Teatro Capitol   
598            Teatro Cine Goya   
599                   Sala Goya   
600          Teatro Reina Sofía   

                                               address  
0    Centro comercial Marineda City\nAvenida Arteix...  
1    Los Cantones Village - Avda. Alférez Provision...  
2    Centro Comercial Espacio Coruña Parcela PIII 1...  
3                  Calle Río Monelos, 1 15006 A Coruña  
4    Centro Comercial As Cancelas\nAvenida Do Camiñ...  
..                                                 ...  
596       Prolongacion Casa Jimenez,s/n 50004 Zaragoza  
597               Plaza San Andrés, 12 50300 Calatayud  
598                     Ramón y Cajal, s/n 50700 Caspe  
599                      Plaza U, s/n 50170 Mequinenza  
600                        Calle Mayor, 55 50800 Zuera  

[601 rows x 2 columns]

In [ ]:
# Obtención de coordenadas por la dirección de cada evento

geolocator = Nominatim(user_agent="cinema_locator")

def geocode_address(address, geolocator, timeout=10, retries=3):
    for attempt in range(retries + 1):
        try:
            location = geolocator.geocode(address, timeout=timeout)
            if location:
                return location.latitude, location.longitude
            return None, None
        except GeocoderTimedOut:
            if attempt < retries:
                time.sleep(2**attempt)  # Retroceso exponencial
                continue
            raise
        except GeocoderServiceError as e:
            print(f"Geocoding service error: {e}")
            return None, None
        except Exception as e:
            print(f"An unexpected error occurred: {e}")
            return None, None
    return None, None

all_cinemas_df['latitude'] = None
all_cinemas_df['longitude'] = None

for index, row in all_cinemas_df.iterrows():
    address = row['address']
    latitude, longitude = geocode_address(address, geolocator)
    all_cinemas_df.loc[index, 'latitude'] = latitude
    all_cinemas_df.loc[index, 'longitude'] = longitude
    time.sleep(1)

print(all_cinemas_df)

print("\nRows with missing coordinates:")
print(all_cinemas_df[all_cinemas_df['latitude'].isnull()])

                           name  \
0          Cinesa Marineda City   
1                Cantones Cines   
2    Yelmo Cines Espacio Coruña   
3     Cines Forum Metropolitano   
4            Cinesa As Cancelas   
..                          ...   
596         Cine Sala Cervantes   
597              Teatro Capitol   
598            Teatro Cine Goya   
599                   Sala Goya   
600          Teatro Reina Sofía   

                                               address   latitude longitude  
0    Centro comercial Marineda City\nAvenida Arteix...       None      None  
1    Los Cantones Village - Avda. Alférez Provision...  43.367653 -8.400271  
2    Centro Comercial Espacio Coruña Parcela PIII 1...       None      None  
3                  Calle Río Monelos, 1 15006 A Coruña  43.355554 -8.398859  
4    Centro Comercial As Cancelas\nAvenida Do Camiñ...       None      None  
..                                                 ...        ...       ...  
596       Prolongacion Casa Jimen

In [94]:
all_cinemas_df

name  \
0          Cinesa Marineda City   
1                Cantones Cines   
2    Yelmo Cines Espacio Coruña   
3     Cines Forum Metropolitano   
4            Cinesa As Cancelas   
..                          ...   
596         Cine Sala Cervantes   
597              Teatro Capitol   
598            Teatro Cine Goya   
599                   Sala Goya   
600          Teatro Reina Sofía   

                                               address   latitude longitude  
0    Centro comercial Marineda City\nAvenida Arteix...       None      None  
1    Los Cantones Village - Avda. Alférez Provision...  43.367653 -8.400271  
2    Centro Comercial Espacio Coruña Parcela PIII 1...       None      None  
3                  Calle Río Monelos, 1 15006 A Coruña  43.355554 -8.398859  
4    Centro Comercial As Cancelas\nAvenida Do Camiñ...       None      None  
..                                                 ...        ...       ...  
596       Prolongacion Casa Jimenez,s/n 50004 Zaragoza       None      None  
597               Plaza San Andrés, 12 50300 Calatayud  41.354999 -1.644959  
598                     Ramón y Cajal, s/n 50700 Caspe  41.238071 -0.041394  
599                      Plaza U, s/n 50170 Mequinenza  41.377576  0.303915  
600                        Calle Mayor, 55 50800 Zuera  41.870027 -0.787189  

[601 rows x 4 columns]

agregando ID a cada cine, creando id's que comienzan en 1 y que contienen 12 dígitos para diferenciarlo de los demás eventos extraídos de otras fuentes

In [ ]:
# Generar una secuencia de ID con ceros a la izquierda
num_cines = len(all_cinemas_df)
start_id = 100000000001
ids = [f"{i:012d}" for i in range(start_id, start_id + num_cines)]

# Insertar la columna 'ID' al comienzo del DataFrame
all_cinemas_df['event_id'] = ids

In [ ]:
# Crear columna tags con la misma información para todos los cines
all_cinemas_df['tags'] = 'cine'

In [ ]:
# Conversión de columnas de coordenadas a tipo flotante
all_cinemas_df[['latitude','longitude']] = all_cinemas_df[['latitude','longitude']].astype(float)

In [105]:
all_cinemas_df.head()

name  \
0        Cinesa Marineda City   
1              Cantones Cines   
2  Yelmo Cines Espacio Coruña   
3   Cines Forum Metropolitano   
4          Cinesa As Cancelas   

                                             address   latitude  longitude  \
0  Centro comercial Marineda City\nAvenida Arteix...        NaN        NaN   
1  Los Cantones Village - Avda. Alférez Provision...  43.367653  -8.400271   
2  Centro Comercial Espacio Coruña Parcela PIII 1...        NaN        NaN   
3                Calle Río Monelos, 1 15006 A Coruña  43.355554  -8.398859   
4  Centro Comercial As Cancelas\nAvenida Do Camiñ...        NaN        NaN   

   tags  
0  cine  
1  cine  
2  cine  
3  cine  
4  cine

In [102]:
all_cinemas_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 601 entries, 0 to 600
Data columns (total 5 columns):
 #   Column     Non-Null Count  Dtype  
---  ------     --------------  -----  
 0   name       601 non-null    object 
 1   address    601 non-null    object 
 2   latitude   279 non-null    float64
 3   longitude  279 non-null    float64
 4   tags       601 non-null    object 
dtypes: float64(2), object(3)
memory usage: 23.6+ KB


Subindo los datos de cinema a la base de datos

In [118]:
all_cinemas_df[['event_id','name','venue_address','latitude','longitude','tags']].head()

event_id                        name  \
0  100000000001        Cinesa Marineda City   
1  100000000002              Cantones Cines   
2  100000000003  Yelmo Cines Espacio Coruña   
3  100000000004   Cines Forum Metropolitano   
4  100000000005          Cinesa As Cancelas   

                                       venue_address venue_address   latitude  \
0  Centro comercial Marineda City\nAvenida Arteix...          None        NaN   
1  Los Cantones Village - Avda. Alférez Provision...          None  43.367653   
2  Centro Comercial Espacio Coruña Parcela PIII 1...          None        NaN   
3                Calle Río Monelos, 1 15006 A Coruña          None  43.355554   
4  Centro Comercial As Cancelas\nAvenida Do Camiñ...          None        NaN   

   longitude  tags  
0        NaN  cine  
1  -8.400271  cine  
2        NaN  cine  
3  -8.398859  cine  
4        NaN  cine

In [ ]:
import os
import psycopg2
from psycopg2.extras import execute_values

# Cargando variable de entorno
RENDER_DB_URI = os.getenv("RENDER_DB_URI")
TABLE_NAME = 'all_events'
UNIQUE_ID_COLUMN = 'event_id'

# Eliminar duplicados en la columna 'venue_address' si existen
all_cinemas_df = all_cinemas_df.loc[:, ~all_cinemas_df.columns.duplicated()]

# Rellene las columnas faltantes con Ninguno
db_columns = [
    'min_age', 'max_age', 'url', 'start_time', 'start_date', 'end_time',
    'end_date', 'duration', 'venue_name', 'venue_address', 'event_id',
    'latitude', 'summary', 'is_online_event', 'tickets_url', 'tags',
    'data_source', 'image', 'age_range', 'longitude', 'name'
]

for col in db_columns:
    if col not in all_cinemas_df.columns:
        all_cinemas_df[col] = None

# Garantizar el orden correcto de las columnas
all_cinemas_df = all_cinemas_df[db_columns]

# Actualizar a PostgreSQL
insert_query = f"""
    INSERT INTO {TABLE_NAME} ({', '.join(db_columns)})
    VALUES %s
    ON CONFLICT ({UNIQUE_ID_COLUMN}) DO UPDATE SET
    {', '.join([f"{col} = EXCLUDED.{col}" for col in db_columns if col != UNIQUE_ID_COLUMN])}
"""

try:
    conn = psycopg2.connect(RENDER_DB_URI)
    cursor = conn.cursor()
    
    values = [tuple(row) for row in all_cinemas_df.to_numpy()]
    
    execute_values(cursor, insert_query, values)
    conn.commit()
    print("✅ Upsert completed successfully.")
    
except Exception as e:
    print(f"❌ Database upsert failed: {e}")
    
finally:
    cursor.close()
    conn.close()


✅ Upsert completed successfully.


In [ ]:
# Construir una tupla de id's insertadas
inserted_ids = tuple(all_cinemas_df['event_id'].tolist())

update_query = f"""
    UPDATE {TABLE_NAME}
    SET data_source = 'cinemas_list'
    WHERE event_id IN %s
"""

try:
    conn = psycopg2.connect(RENDER_DB_URI)
    cursor = conn.cursor()

    cursor.execute(update_query, (inserted_ids,))
    conn.commit()
    print("✅ data_source updated to 'cinemas_list' for relevant rows.")
    
except Exception as e:
    print(f"❌ Failed to update data_source: {e}")
    
finally:
    cursor.close()
    conn.close()

✅ data_source updated to 'cinemas_list' for relevant rows.


---------------------------------------

webscraping datos de sitio sobre eventos para niños

In [5]:
letras_url = "https://www.planinfantil.es/planes-gratis-con-ninos-en-madrid/"
url_obtenido = requests.get(letras_url)
soup = BeautifulSoup(url_obtenido.text, "html.parser")

# Buscar todos los contenedores de eventos
events_container = soup.find_all('div', class_='wp-block-toolset-blocks-container tb-container')

# Listas para almacenar datos extraídos
events_list_url = []
events_list_title = []
events_list_date = []
events_list_address = []

# Iterar a través de cada contenedor de eventos
for event in events_container:
    try:
        # Obtener el enlace de la imagen / URL del evento
        figure_tag = event.find('figure')
        if figure_tag and figure_tag.find('a'):
            event_url = figure_tag.find('a')['href']
        else:
            continue  # Omitir si no hay URL de evento

        # Obtener título
        title_tag = event.find('h6')
        event_title = title_tag.get_text(strip=True) if title_tag else ""

        # Obtener fecha y dirección
        text_blocks = event.find_all('div', class_='tb-fields-and-text')
        event_date = text_blocks[0].get_text(strip=True) if len(text_blocks) > 0 else ""
        event_address = text_blocks[1].get_text(strip=True) if len(text_blocks) > 1 else ""

        # Añadir a listas
        events_list_url.append(event_url)
        events_list_title.append(event_title)
        events_list_date.append(event_date)
        events_list_address.append(event_address)

    except Exception as e:
        print("Error processing event:", e)

# Crear el DataFrame
df = pd.DataFrame({
    'URL': events_list_url,
    'Title': events_list_title,
    'Date': events_list_date,
    'Place/Price': events_list_address
})

print(df.head())


                                                                                                          URL  \
0         https://www.planinfantil.es/plan/ihe-y-los-sonidos-del-nilo-cuentacuentos-en-el-museo-arqueologico/   
1                       https://www.planinfantil.es/plan/andresillo-y-el-dragon-aventuras-en-el-arqueologico/   
2                     https://www.planinfantil.es/plan/los-sonidos-de-la-antiguedad-en-el-museo-arqueologico/   
3  https://www.planinfantil.es/plan/hipolita-una-reina-de-armas-tomar-cuentacuentos-en-el-museo-arqueologico/   
4                       https://www.planinfantil.es/plan/junia-una-romana-en-apuros-en-el-museo-arqueologico/   

                                                                        Title  \
0          Ihé y los sonidos del Nilo, cuentacuentos en el Museo Arqueológico   
1                        Andresillo y el dragón. Aventuras en el Arqueológico   
2                       Los sonidos de la antigüedad en el Museo Arqueológico 

In [6]:
df.head()

URL  \
0         https://www.planinfantil.es/plan/ihe-y-los-sonidos-del-nilo-cuentacuentos-en-el-museo-arqueologico/   
1                       https://www.planinfantil.es/plan/andresillo-y-el-dragon-aventuras-en-el-arqueologico/   
2                     https://www.planinfantil.es/plan/los-sonidos-de-la-antiguedad-en-el-museo-arqueologico/   
3  https://www.planinfantil.es/plan/hipolita-una-reina-de-armas-tomar-cuentacuentos-en-el-museo-arqueologico/   
4                       https://www.planinfantil.es/plan/junia-una-romana-en-apuros-en-el-museo-arqueologico/   

                                                                        Title  \
0          Ihé y los sonidos del Nilo, cuentacuentos en el Museo Arqueológico   
1                        Andresillo y el dragón. Aventuras en el Arqueológico   
2                       Los sonidos de la antigüedad en el Museo Arqueológico   
3  Hipólita, una reina de armas tomar, cuentacuentos en el Museo Arqueológico   
4                        Junia, una romana en apuros en el Museo Arqueológico   

                           Date      Place/Price  
0  Del 11/01/2025 al 07/06/2025  Madrid – Gratis  
1  Del 11/01/2025 al 21/06/2025  Madrid – Gratis  
2  Del 18/01/2025 al 14/06/2025  Madrid – Gratis  
3  Del 25/01/2025 al 10/05/2025  Madrid – Gratis  
4  Del 15/02/2025 al 24/05/2025  Madrid – Gratis

--------------------------------------------------------------------

Recopilar datos del sitio web Eventbrite, filtrados para recibir solo eventos para niños

In [7]:
base_url = "https://www.eventbrite.com/"
target_url = "d/spain/all-events/?subcategories=15003%2C15004%2C15005%2C15006&page=1"


headers = {
    "accept": "*/*",
    "accept-language": "en-US,en;q=0.9,it-IT;q=0.8,it;q=0.7,pt;q=0.6,es;q=0.5",
    "priority": "u=1, i",
    "referer": "https://www.eventbrite.com/d/spain/all-events/?subcategories=15003%2C15004%2C15005%2C15006&page=1",
    "sec-ch-ua": '"Google Chrome";v="135", "Not-A.Brand";v="8", "Chromium";v="135"',
    "sec-ch-ua-mobile": "?0",
    "sec-ch-ua-platform": '"Windows"',
    "sec-fetch-dest": "empty",
    "sec-fetch-mode": "cors",
    "sec-fetch-site": "same-origin",
    "user-agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/135.0.0.0 Safari/537.36",
    "x-csrftoken": "6a8e093a186e11f0b3df7333c3540c62",
    "x-requested-with": "XMLHttpRequest"
}

In [8]:
resp = requests.get(f'{base_url}/{target_url}', headers=headers)

In [9]:
print(resp.status_code)

200


In [10]:
soup = BeautifulSoup(resp.text, 'html.parser')

In [11]:
soup

{"search_data":{"articles":{},"current_user_id":null,"profile_search":{},"article_search":{},"profiles":{},"events":{"pagination":{"object_count":23,"page_count":2,"page_number":1,"page_size":20,"continuation":"eyJwYWdlIjoyfQ"},"results":[{"image":{"edge_color_set":true,"edge_color":"#5e624b","url":"https://img.evbuc.com/https%3A%2F%2Fcdn.evbuc.com%2Fimages%2F930362993%2F1055957277713%2F1%2Foriginal.20250108-094813?w=512\u0026auto=format%2Ccompress\u0026q=75\u0026sharp=10\u0026rect=0%2C1017%2C7008%2C3504\u0026s=7a92281f824dcd2a8c425567ebf482f8","id":"930362993","crop_mask":{"width":7008,"height":3504,"top_left":{"y":1017,"x":0}},"aspect_ratio":2.0,"focal_point":null,"original":{"url":"https://img.evbuc.com/https%3A%2F%2Fcdn.evbuc.com%2Fimages%2F930362993%2F1055957277713%2F1%2Foriginal.20250108-094813?auto=format%2Ccompress\u0026q=75\u0026sharp=10\u0026s=b174472cd3afab38a581d4e948b3a7aa","width":7008,"height":4672}},"timezone":"Europe/Madrid","id":"1307028560609","tickets_url":"https://

In [ ]:
url = "https://www.eventbrite.com/d/spain/all-events/?subcategories=15003%2C15004%2C15005%2C15006&page=1"

headers = {
    "accept": "*/*",
    "accept-language": "en-US,en;q=0.9,it-IT;q=0.8,it;q=0.7,pt;q=0.6,es;q=0.5",
    "priority": "u=1, i",
    "referer": "https://www.eventbrite.com/d/spain/all-events/?subcategories=15003%2C15004%2C15005%2C15006&page=1",
    "sec-ch-ua": '"Google Chrome";v="135", "Not-A.Brand";v="8", "Chromium";v="135"',
    "sec-ch-ua-mobile": "?0",
    "sec-ch-ua-platform": '"Windows"',
    "sec-fetch-dest": "empty",
    "sec-fetch-mode": "cors",
    "sec-fetch-site": "same-origin",
    "user-agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/135.0.0.0 Safari/537.36",
    "x-csrftoken": "6a8e093a186e11f0b3df7333c3540c62",
    "x-requested-with": "XMLHttpRequest"
}

cookies = {
    "mgrefby": "https://www.google.com/",
    "guest": "identifier=75b1ab71-48c3-4d01-ad8a-782d93c1f5b6&a=13e8&s=3411e4860099bda2b7af7214fd17839fbe2e76413c4fea6258e306e45ffcc717",
    "G": "v=2&i=75b1ab71-48c3-4d01-ad8a-782d93c1f5b6&a=13e8&s=b30ebeb1875f2120a85bd6000eefa890f9f4cf55",
    "csrftoken": "6a8e093a186e11f0b3df7333c3540c62",
    "session": "identifier=822257312e8c43ce8e9bec649fedd725&issuedTs=1744553017&originalTs=1744552296&s=1815426704c353afae38072c44048b429f12aa1d9f323757b7e9fbecd97c17ff"
}

response = requests.get(url, headers=headers, cookies=cookies)

if response.status_code == 200:
    data = response.json()
    search_data = data.get("search_data")
    if search_data and "events" in search_data:
        events = search_data["events"].get("results", [])
        extracted_data = []
        for event in events:
            start_time_str = event.get("start_date") + " " + event.get("start_time") if event.get("start_date") and event.get("start_time") else None
            end_time_str = event.get("end_date") + " " + event.get("end_time") if event.get("end_date") and event.get("end_time") else None
            duration = None
            image_url = event.get("image", {}).get("url")
            venue = event.get("primary_venue", {})
            address = venue.get("address", {})
            longitude = float(address.get("longitude"))
            latitude = float(address.get("latitude"))

            if start_time_str and end_time_str:
                try:
                    start_datetime = datetime.fromisoformat(start_time_str)
                    end_datetime = datetime.fromisoformat(end_time_str)
                    duration = str(end_datetime - start_datetime)
                except ValueError:
                    duration = "Invalid date/time format"

            image_html = f'<img src="{image_url}" width="100" height="100">' if image_url else "No Image"

            item = {
                "name": event.get("name"),
                "url": event.get("url"),
                "image": HTML(image_html),  # Almacenar el objeto HTML
                "start_time": event.get("start_time"),
                "start_date": event.get("start_date"),
                "end_time": event.get("end_time"),
                "end_date": event.get("end_date"),
                "duration": duration,
                "venue_name": event.get("primary_venue", {}).get("name"),
                "venue_address": event.get("primary_venue", {}).get("address", {}).get("localized_address_display"),
                "longitude": longitude,
                "latitude": latitude,
                "summary": event.get("summary"),
                "is_online_event": event.get("is_online_event"),
                "tickets_url": event.get("tickets_url"),
                "tags": [tag.get("display_name") for tag in event.get("tags", [])],
                "event_id": event.get("id"),
                "data_source": "eventbrite"
            }
            extracted_data.append(item)

        # Imprimir los datos extraídos en la salida de Jupyter
        for item in extracted_data:
            print(f"Name: {item['name']}")
            print(f"URL: {item['url']}")
            display(item['image'])  # Utilizar display() para renderizar el HTML
            print(f"Start date: {item['start_date']} | End date: {item['end_date']}")
            print(f"Start Time: {item['start_time']}")
            print(f"End Time: {item['end_time']}")
            print(f"Duration: {item['duration']}")
            print("-" * 60)

    else:
        print("Could not find 'events' data in the JSON response.")
else:
    print("Failed to retrieve data:", response.status_code)

Name: Cuánto Cuento!  (de 0 a 6 años)
URL: https://www.eventbrite.es/e/entradas-cuanto-cuento-de-0-a-6-anos-1307028560609


Start date: 2025-04-19 | End date: 2025-04-19
Start Time: 11:30
End Time: 12:00
Duration: 0:30:00
------------------------------------------------------------
Name: Club Futuros Podcasters - Taller de podcast para niños de 6 a 12 años
URL: https://www.eventbrite.es/e/entradas-club-futuros-podcasters-taller-de-podcast-para-ninos-de-6-a-12-anos-1297237354849


Start date: 2025-05-08 | End date: 2025-05-08
Start Time: 17:30
End Time: 18:30
Duration: 1:00:00
------------------------------------------------------------
Name: Jugar el arte en familia 3 DE MAYO
URL: https://www.eventbrite.es/e/entradas-jugar-el-arte-en-familia-3-de-mayo-1302039748939


Start date: 2025-05-03 | End date: 2025-05-03
Start Time: 16:30
End Time: 17:30
Duration: 1:00:00
------------------------------------------------------------
Name: Taller FAMILIAR de Lettering  ¡DIBUJAMOS EL ABECEDARIO!
URL: https://www.eventbrite.es/e/taller-familiar-de-lettering-dibujamos-el-abecedario-tickets-1312720154319


Start date: 2025-05-10 | End date: 2025-05-10
Start Time: 10:00
End Time: 12:00
Duration: 2:00:00
------------------------------------------------------------
Name: Investigactiva. Especial Energía y movimiento 18 DE MAYO
URL: https://www.eventbrite.es/e/investigactiva-especial-energia-y-movimiento-18-de-mayo-tickets-1302072707519


...

Start date: 2025-04-27 | End date: 2025-04-27
Start Time: 11:00
End Time: 12:00
Duration: 1:00:00
------------------------------------------------------------
Name: EL REMENDÓN DE LA MUERTE  (MENUTSBARRIS) Títelles (+ 6 años).
URL: https://www.eventbrite.es/e/entradas-el-remendon-de-la-muerte-menutsbarris-titelles-6-anos-1279173094159


Start date: 2025-05-09 | End date: 2025-05-09
Start Time: 18:30
End Time: 19:30
Duration: 1:00:00
------------------------------------------------------------
Name: ÉRASE UNA VEZ UN PATO_Teatro la proa_(MENUTSBARRIS).
URL: https://www.eventbrite.es/e/entradas-erase-una-vez-un-pato-teatro-la-proa-menutsbarris-1277765845039


Start date: 2025-05-09 | End date: 2025-05-09
Start Time: 18:30
End Time: 19:30
Duration: 1:00:00
------------------------------------------------------------
Name: Retratar el alma: retratos de libertad 10 DE MAYO
URL: https://www.eventbrite.es/e/entradas-retratar-el-alma-retratos-de-libertad-10-de-mayo-1300677063109


Start date: 2025-05-10 | End date: 2025-05-10
Start Time: 17:00
End Time: 18:00
Duration: 1:00:00
------------------------------------------------------------
Name: Muchas Caperucitas y algún lobo bueno 11 DE MAYO
URL: https://www.eventbrite.es/e/entradas-muchas-caperucitas-y-algun-lobo-bueno-11-de-mayo-1318017970229


Start date: 2025-05-11 | End date: 2025-05-11
Start Time: 11:00
End Time: 12:00
Duration: 1:00:00
------------------------------------------------------------


In [13]:
eventbrite_df = pd.DataFrame(extracted_data)

In [14]:
eventbrite_df.head()

name  \
0                                        Cuánto Cuento!  (de 0 a 6 años)   
1  Club Futuros Podcasters - Taller de podcast para niños de 6 a 12 años   
2                                     Jugar el arte en familia 3 DE MAYO   
3                Taller FAMILIAR de Lettering  ¡DIBUJAMOS EL ABECEDARIO!   
4               Investigactiva. Especial Energía y movimiento 18 DE MAYO   

                                                                                                                      url  \
0                                          https://www.eventbrite.es/e/entradas-cuanto-cuento-de-0-a-6-anos-1307028560609   
1  https://www.eventbrite.es/e/entradas-club-futuros-podcasters-taller-de-podcast-para-ninos-de-6-a-12-anos-1297237354849   
2                                   https://www.eventbrite.es/e/entradas-jugar-el-arte-en-familia-3-de-mayo-1302039748939   
3                  https://www.eventbrite.es/e/taller-familiar-de-lettering-dibujamos-el-abecedario-tickets-1312720154319   
4               https://www.eventbrite.es/e/investigactiva-especial-energia-y-movimiento-18-de-mayo-tickets-1302072707519   

                                image start_time  start_date end_time  \
0  <IPython.core.display.HTML object>      11:30  2025-04-19    12:00   
1  <IPython.core.display.HTML object>      17:30  2025-05-08    18:30   
2  <IPython.core.display.HTML object>      16:30  2025-05-03    17:30   
3  <IPython.core.display.HTML object>      10:00  2025-05-10    12:00   
4  <IPython.core.display.HTML object>      11:30  2025-05-18    12:25   

     end_date duration                           venue_name  \
0  2025-04-19  0:30:00  Vualá - Librería juvenil y infantil   
1  2025-05-08  1:00:00               C. de Ramón y Cajal, 4   
2  2025-05-03  1:00:00                      Casa del Lector   
3  2025-05-10  2:00:00               Tienda Cuadernos RUBIO   
4  2025-05-18  0:55:00                      Casa del Lector   

                                                                              venue_address  \
0  17 Calle de Santa Feliciana Calle Santa Feliciana 17, 28010 Madrid, España, 28010 Madrid   
1                                         4 Calle de Ramón y Cajal, 28801 Alcalá de Henares   
2                                                      14 Paseo de la Chopera, 28045 Madrid   
3                                           9 Carrer de Sorní #bajo derecha, 46004 València   
4                                                      14 Paseo de la Chopera, 28045 Madrid   

   longitude   latitude  \
0  -3.698552  40.433543   
1  -3.365515  40.482542   
2  -3.698443  40.392663   
3  -0.368432  39.470320   
4  -3.698443  40.392663   

                                                                                                                                       summary  \
0                     ¡Ven y disfruta de una mañana llena de historias, risas y diversión en nuestros cuenta cuentos, junto a Factoría Teatro!   
1  Talleres de podcast mensuales para niños. Nos reunimos el primer jueves de cada mes. Ven a probar un taller o apúntate a todos hasta julio.   
2                                                                                                                  Explorando y creando juntos   
3                Ven y aprende a dibujar letras de forma creativa en familia en nuestro taller de lettering, ¡te esperamos en la tienda RUBIO!   
4                                                                       Espacio de experimentación científica para niñas y niños de 2 a 8 años   

   is_online_event  \
0            False   
1            False   
2            False   
3            False   
4            False   

                                                      tickets_url  \
0  https://www.eventbrite.com/checkout-external?eid=1307028560609   
1  https://www.eventbrite.com/checkout-external?eid=1297237354849   
2  https://www.eventbrite.com/checkout-external?eid=1302039748939   
3  https://www.eventbr

In [15]:
# Generando el mapa a partir de las coordenadas

# Crea un mapa base centrado en España
spain_latitude = 40.4637
spain_longitude = -3.7492
event_map = folium.Map(location=[spain_latitude, spain_longitude], zoom_start=7)

# Iterar a través del DataFrame y agregar marcadores
for _, row in eventbrite_df.iterrows():
    popup_html = f"""
    <strong>{row['name']}</strong><br>
    📍 <em>{row['venue_name']}</em><br>
    🗓 {row['start_date']} {row['start_time']} - {row['end_time']}<br>
    <a href="{row['url']}" target="_blank">Ver evento</a>
    """
    folium.Marker(
        location=[row['latitude'], row['longitude']],
        popup=folium.Popup(popup_html, max_width=300),
        tooltip=row['name']
    ).add_to(event_map)

# Guardar en HTML:
event_map.save("event_map.html")

# o mostrar en el notebook:
event_map


--------------------------------------------------------

Extraci'on de datos la ADI datos.madrid.es (Comunidad de Madrid)

In [16]:
# descargando los datos de Agenda de actividades y eventos de la API del Portal de datos abiertos del Ayuntamiento de Madrid

url = "https://datos.madrid.es/egob/catalogo/300107-0-agenda-actividades-eventos.json"

try:
    response = requests.get(url)
    response.raise_for_status()
    raw_text = response.text
    cleaned_text = re.sub(r"\\(?![nrtbf\"\\/])", "", raw_text)
    data = json.loads(cleaned_text)

    if isinstance(data, dict):
        print(f"Top-level dictionary keys: {data.keys()}")
        if '@graph' in data and isinstance(data['@graph'], list):
            df = pd.DataFrame(data['@graph'])
            print(df.head())
        else:
            print("The list of events was not found within the '@graph' key.")
    else:
        print("Parsed JSON is not a dictionary as expected.")

except requests.exceptions.RequestException as e:
    print(f"Error fetching data: {e}")
except json.JSONDecodeError as e:
    print(f"Error decoding JSON: {e}")
except Exception as e:
    print(f"An unexpected error occurred: {e}")

Top-level dictionary keys: dict_keys(['@context', '@graph'])
                                                                                                                      @id  \
0                     https://datos.madrid.es/egob/catalogo/tipo/evento/12733698-150-anos-nacimiento-antonio-machado.json   
1  https://datos.madrid.es/egob/catalogo/tipo/evento/12735098-150-anos-nacimiento-antonio-machado-teatro-ojos-poeta-.json   
2                                https://datos.madrid.es/egob/catalogo/tipo/evento/12734393-2-encuentro-estuve-alli-.json   
3                         https://datos.madrid.es/egob/catalogo/tipo/evento/12750408-6-sesion-poetas-americas-madrid.json   
4                https://datos.madrid.es/egob/catalogo/tipo/evento/12747998-75-aniversario-adhesion-hortaleza-madrid.json   

                                                                  @type  \
0    https://datos.madrid.es/egob/kos/actividades/ConferenciasColoquios   
1  https://datos.madrid.es/egob/kos/ac

In [17]:
# Descubriendo los tipos de público registrados en el dataset para luego filtrar por las categorias que nos interesan
df['audience'].unique()

array([nan, 'Familias', 'Niños', 'Jovenes,Niños', 'Jovenes', 'Mayores',
       'Mujeres', 'Niños,Familias', 'Mujeres,Mayores',
       'Jovenes,Niños,Familias', 'EmpresariosYComerciantes',
       'Discapacitados', 'Familias,Mayores',
       'Jovenes,EstudianteseInvestigadores'], dtype=object)

In [18]:
# Haciendo el filtrado del dataset
filtered_df = df[df['audience'].isin(['Familias', 'Niños', 'Jovenes,Niños', 'Niños,Familias', 'Jovenes,Niños,Familias'])]

In [19]:
filtered_df.head(1)

@id  \
1  https://datos.madrid.es/egob/catalogo/tipo/evento/12735098-150-anos-nacimiento-antonio-machado-teatro-ojos-poeta-.json   

                                                                  @type  \
1  https://datos.madrid.es/egob/kos/actividades/ComemoracionesHomenajes   

         id                                                             title  \
1  12735098  150 AÑOS NACIMIENTO ANTONIO MACHADO. Teatro: 'Con ojos de poeta'   

                                                                                                                                                                                                                                                                                                                                                                                            description  \
1  Dramaturgia: Jesús Novo- Poesías: Antonio Machado Con:- Sonsoles Novo (Dirección artística e intérprete). Álida Jiménez (Dirección Musical e intérprete: voz y guitarra). En la casa de Petrita, que fue alumna de Don Antonio Machado, cada vez que se retira una tela aparece un objeto relacionado con la vida y la obra de Machado.  Edad recomendada: público adulto y apto a partir de 8 años.   

   free price                dtstart                  dtend   time  ...  \
1     1        2025-04-25 18:30:00.0  2025-04-25 23:59:00.0  18:30  ...   

        uid  \
1  12735098   

                                                                                                                                               link  \
1  http://www.madrid.es/sites/v/index.jsp?vgnextchannel=ca9671ee4a9eb410VgnVCM100000171f5a0aRCRD&vgnextoid=39af8b56808d5910VgnVCM2000001f4a900aRCRD   

                                              event-location  \
1  Centro Sociocultural Montecarmelo (Fuencarral - El Pardo)   

                                                                                                                                                    references  \
1  {'@id': 'http://www.madrid.es/sites/v/index.jsp?vgnextchannel=ca9671ee4a9eb410VgnVCM100000171f5a0aRCRD&vgnextoid=a2fea399e519c810VgnVCM1000001d4a900aRCRD'}   

                                                                                                                                      relation  \
1  {'@id': 'https://datos.madrid.es/egob/catalogo/tipo/entidadesyorganismos/5514552-centro-sociocultural-montecarmelo-fuencarral-pardo-.json'}   

                                                                                                                                                                                                                                                                                                                                                     address  \
1  {'district': {'@id': 'https://datos.madrid.es/egob/kos/Provincia/Madrid/Municipio/Madrid/Distrito/Fuencarral-ElPardo'}, 'area': {'@id': 'https://datos.madrid.es/egob/kos/Provincia/Madrid/Municipio/Madrid/Distrito/Fuencarral-ElPardo/Barrio/ElGoloso', 'locality': 'MADRID', 'postal-code': '28049', 'street-address': 'Carretera M-607 Km 13 L-10 '}}   

                                                             location  \
1  {'latitude': 40.515712291624084, 'longitude': -3.6860532895354448}   

                                                                                              organization  \
1  {'organization-name': 'Centro Sociocultural Montecarmelo (Fuencarral - El Pardo)', 'accesibility': '1'}   

   audience recurrence  
1  Familias        NaN  

[1 rows x 21 columns]

In [20]:
# Filtrando el dataset por valores nulos en las columnas que hacen referencia a la ubicación del evento
filtered_df[filtered_df['address'].isna() & filtered_df['location'].isna()].head()

@id  \
117      https://datos.madrid.es/egob/catalogo/tipo/evento/12702034-campamento-verano-2025-puente-vallecas.json   
118  https://datos.madrid.es/egob/catalogo/tipo/evento/12752479-campamento-verano-2025-distrito-villaverde.json   
123           https://datos.madrid.es/egob/catalogo/tipo/evento/12683216-campamento-urbano-primavera-usera.json   
126              https://datos.madrid.es/egob/catalogo/tipo/evento/12753682-campamento-urbano-verano-usera.json   
135      https://datos.madrid.es/egob/catalogo/tipo/evento/12741335-caracterizacion-actividades-infantiles.json   

                                                                                   @type  \
117              https://datos.madrid.es/egob/kos/actividades/ActividadesCalleArteUrbano   
118                             https://datos.madrid.es/egob/kos/actividades/Campamentos   
123                             https://datos.madrid.es/egob/kos/actividades/Campamentos   
126                             https://datos.madrid.es/egob/kos/actividades/Campamentos   
135  https://datos.madrid.es/egob/kos/actividades/RecitalesPresentacionesActosLiterarios   

           id                                                title  \
117  12702034      Campamento de verano 2025 en Puente de Vallecas   
118  12752479  Campamento de Verano 2025 -  Distrito de Villaverde   
123  12683216              Campamento urbano de primavera en Usera   
126  12753682                 Campamento urbano de verano en Usera   
135  12741335             Caracterización y actividades infantiles   

                                                                                                  description  \
117                                                                                                             
118                                                                                                             
123                                                                                                             
126                                                                                                             
135  Caracterización y actividades infantiles entorno al Siglo de Oro. Lugar: Paseo del Prado 36 (CaixaFoum).   

     free price                dtstart                  dtend   time  ...  \
117     1        2025-06-23 00:00:00.0  2025-09-05 23:59:00.0         ...   
118     1        2025-06-23 00:00:00.0  2025-07-31 23:59:00.0         ...   
123     1        2025-04-11 00:00:00.0  2025-04-21 23:59:00.0         ...   
126     1        2025-07-01 00:00:00.0  2025-09-05 23:59:00.0         ...   
135     1        2025-04-24 17:00:00.0  2025-04-24 23:59:00.0  17:00  ...   

          uid  \
117  12702034   
118  12752479   
123  12683216   
126  12753682   
135  12741335   

                                                                                                                                                 link  \
117  http://www.madrid.es/sites/v/index.jsp?vgnextchannel=ca9671ee4a9eb410VgnVCM100000171f5a0aRCRD&vgnextoid=5c4cb1e2d1745910VgnVCM1000001d4a900aRCRD   
118  http://www.madrid.es/sites/v/index.jsp?vgnextchannel=ca9671ee4a9eb410VgnVCM100000171f5a0aRCRD&vgnextoid=50838bbda3026910VgnVCM2000001f4a900aRCRD   
123  http://www.madrid.es/sites/v/index.jsp?vgnextchannel=ca9671ee4a9eb410VgnVCM100000171f5a0aRCRD&vgnextoid=9441898ec60f4910VgnVCM2000001f4a900aRCRD   
126  http://www.madrid.es/sites/v/index.jsp?vgnextchannel=ca9671ee4a9eb410VgnVCM100000171f5a0aRCRD&vgnextoid=514e2e4d2e136910VgnVCM2000001f4a900aRCRD   
135  http://www.madrid.es/sites/v/index.jsp?vgnextchannel=ca9671ee4a9eb410VgnVCM100000171f5a0aRCRD&vgnextoid=fa285b230f5f5910VgnVCM2000001f4a900aRCRD   

    event-location  \
117                  
118                  
123                  
126                  
135                  

                                                                                                                                                  

In [21]:
extracted_data = []
for index, row in filtered_df.iterrows():
    extracted_event = {
        "name": row["title"],
        "url": row["link"],
        "image": None,
        "start_time": row["time"],
        "start_date": pd.to_datetime(row["dtstart"]).date() if pd.notna(row["dtstart"]) else None,
        "end_time": None,
        "end_date": pd.to_datetime(row["dtend"]).date() if pd.notna(row["dtend"]) else None,
        "duration": None,
        "venue_name": row["event-location"],
        "venue_address": row["address"].get("area", {}).get("street-address")
                         if isinstance(row["address"], dict) else None,
        "longitude": row["location"].get("longitude")
                         if isinstance(row["location"], dict) else None, # Comprueba si la ubicación es un diccionario
        "latitude": row["location"].get("latitude")
                        if isinstance(row["location"], dict) else None, # Comprueba si la ubicación es un diccionario
        "summary": row["description"],
        "is_online_event": None,
        "tickets_url": row["link"],
        "tags": [row["audience"]] if pd.notna(row["audience"]) else [],
        "event_id": row["uid"],
        "data_source": "ayuntamiento madrid"
    }
    extracted_data.append(extracted_event)

ayuntamiento_madrid_df = pd.DataFrame(extracted_data)
print(ayuntamiento_madrid_df.head())
print(ayuntamiento_madrid_df.info())

                                                               name  \
0  150 AÑOS NACIMIENTO ANTONIO MACHADO. Teatro: 'Con ojos de poeta'   
1                                                   A la mar salada   
2                                               A taste of the moon   
3                                               A taste of the moon   
4                                               A taste of the moon   

                                                                                                                                                url  \
0  http://www.madrid.es/sites/v/index.jsp?vgnextchannel=ca9671ee4a9eb410VgnVCM100000171f5a0aRCRD&vgnextoid=39af8b56808d5910VgnVCM2000001f4a900aRCRD   
1  http://www.madrid.es/sites/v/index.jsp?vgnextchannel=ca9671ee4a9eb410VgnVCM100000171f5a0aRCRD&vgnextoid=366f468e9b336910VgnVCM1000001d4a900aRCRD   
2  http://www.madrid.es/sites/v/index.jsp?vgnextchannel=ca9671ee4a9eb410VgnVCM100000171f5a0aRCRD&vgnextoid=edd0528353436

In [22]:
ayuntamiento_madrid_df.head()

name  \
0  150 AÑOS NACIMIENTO ANTONIO MACHADO. Teatro: 'Con ojos de poeta'   
1                                                   A la mar salada   
2                                               A taste of the moon   
3                                               A taste of the moon   
4                                               A taste of the moon   

                                                                                                                                                url  \
0  http://www.madrid.es/sites/v/index.jsp?vgnextchannel=ca9671ee4a9eb410VgnVCM100000171f5a0aRCRD&vgnextoid=39af8b56808d5910VgnVCM2000001f4a900aRCRD   
1  http://www.madrid.es/sites/v/index.jsp?vgnextchannel=ca9671ee4a9eb410VgnVCM100000171f5a0aRCRD&vgnextoid=366f468e9b336910VgnVCM1000001d4a900aRCRD   
2  http://www.madrid.es/sites/v/index.jsp?vgnextchannel=ca9671ee4a9eb410VgnVCM100000171f5a0aRCRD&vgnextoid=edd0528353436910VgnVCM2000001f4a900aRCRD   
3  http://www.madrid.es/sites/v/index.jsp?vgnextchannel=ca9671ee4a9eb410VgnVCM100000171f5a0aRCRD&vgnextoid=7911528353436910VgnVCM2000001f4a900aRCRD   
4  http://www.madrid.es/sites/v/index.jsp?vgnextchannel=ca9671ee4a9eb410VgnVCM100000171f5a0aRCRD&vgnextoid=2c4e528353436910VgnVCM2000001f4a900aRCRD   

  image start_time  start_date end_time    end_date duration  \
0  None      18:30  2025-04-25     None  2025-04-25     None   
1  None      18:00  2025-05-09     None  2025-05-09     None   
2  None      17:30  2025-05-22     None  2025-05-22     None   
3  None      17:30  2025-05-29     None  2025-05-29     None   
4  None      18:00  2025-05-07     None  2025-05-07     None   

                                                       venue_name  \
0       Centro Sociocultural Montecarmelo (Fuencarral - El Pardo)   
1      Biblioteca Pública Municipal Ciudad Lineal (Ciudad Lineal)   
2       Biblioteca Pública Municipal Pablo Neruda (Ciudad Lineal)   
3  Biblioteca Pública Municipal Manuel Vázquez Montalbán (Tetuán)   
4  Biblioteca Pública Municipal José Hierro (San Blas-Canillejas)   

                       venue_address  longitude   latitude  \
0        Carretera M-607 Km 13 L-10   -3.686053  40.515712   
1  CALLE HERMANOS GARCIA NOBLEJAS 14  -3.637292  40.436447   
2                      CALLE ASCAO 4  -3.641690  40.429411   
3         CALLE FRANCOS RODRIGUEZ 67  -3.710540  40.457495   
4       CALLE MARIA SEVILLA DIAGO 15  -3.610566  40.433292   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  summary  \
0                                                                                                                                                                                                                                    Dramaturgia: Jesús Novo- Poesías: Antonio Machado Con:- Sonsoles Novo (Dirección artística e intérprete). Álida Jiménez (Dirección Musical e intérprete: voz y guitarra). En la casa de Petrita, que fue alumna de Don Antonio Machado, cada vez que se retira una tela aparece un objeto relacionado con la vida y la obra de Machado.  Edad recomendada: público adulto y apto a partir de 8 años.   
1                                                                                                                            Duendes, tesoros, aventuras, misterios... Las bibliotecas están llenas de historias que cuenteros y cuenteras nos acercan a través de su creatividad y su magia.  Este cuento está pensado pa

In [23]:
# Generando el mapa a partir de las coordenadas

# Filtrar filas donde la latitud o longitud es NaN
valid_events_df = ayuntamiento_madrid_df.dropna(subset=['latitude', 'longitude'])

if not valid_events_df.empty:
    # Crea un mapa base centrado en España
    spain_latitude = 40.4637
    spain_longitude = -3.7492
    event_map = folium.Map(location=[spain_latitude, spain_longitude], zoom_start=7)

    # Iterar a través del DataFrame filtrado y agregar marcadores
    for _, row in valid_events_df.iterrows():
        popup_html = f"""
        <strong>{row['name']}</strong><br>
        📍 <em>{row['venue_name']}</em><br>
        🗓 {row['start_date']} {row['start_time']} - {row['end_time']}<br>
        <a href="{row['url']}" target="_blank">Ver evento</a>
        """
        folium.Marker(
            location=[row['latitude'], row['longitude']],
            popup=folium.Popup(popup_html, max_width=300),
            tooltip=row['name']
        ).add_to(event_map)

    # Guardar como HTML:
    event_map.save("event_map.html")
    # o mostrar en el notebook:
    event_map
else:
    print("No events with valid latitude and longitude to display on the map.")

In [24]:
event_map

---------------------------------------------

Concatenando los dataframes

In [ ]:
# Creando una lista con los datasets existentes
dataframes_list = [eventbrite_df, ayuntamiento_madrid_df]

In [26]:
# Concatenando los dataframes
combined_df = pd.concat(dataframes_list, ignore_index=True)

In [27]:
combined_df = combined_df.drop(columns='image')

In [28]:
combined_df.head()

name  \
0                                        Cuánto Cuento!  (de 0 a 6 años)   
1  Club Futuros Podcasters - Taller de podcast para niños de 6 a 12 años   
2                                     Jugar el arte en familia 3 DE MAYO   
3                Taller FAMILIAR de Lettering  ¡DIBUJAMOS EL ABECEDARIO!   
4               Investigactiva. Especial Energía y movimiento 18 DE MAYO   

                                                                                                                      url  \
0                                          https://www.eventbrite.es/e/entradas-cuanto-cuento-de-0-a-6-anos-1307028560609   
1  https://www.eventbrite.es/e/entradas-club-futuros-podcasters-taller-de-podcast-para-ninos-de-6-a-12-anos-1297237354849   
2                                   https://www.eventbrite.es/e/entradas-jugar-el-arte-en-familia-3-de-mayo-1302039748939   
3                  https://www.eventbrite.es/e/taller-familiar-de-lettering-dibujamos-el-abecedario-tickets-1312720154319   
4               https://www.eventbrite.es/e/investigactiva-especial-energia-y-movimiento-18-de-mayo-tickets-1302072707519   

  start_time  start_date end_time    end_date duration  \
0      11:30  2025-04-19    12:00  2025-04-19  0:30:00   
1      17:30  2025-05-08    18:30  2025-05-08  1:00:00   
2      16:30  2025-05-03    17:30  2025-05-03  1:00:00   
3      10:00  2025-05-10    12:00  2025-05-10  2:00:00   
4      11:30  2025-05-18    12:25  2025-05-18  0:55:00   

                            venue_name  \
0  Vualá - Librería juvenil y infantil   
1               C. de Ramón y Cajal, 4   
2                      Casa del Lector   
3               Tienda Cuadernos RUBIO   
4                      Casa del Lector   

                                                                              venue_address  \
0  17 Calle de Santa Feliciana Calle Santa Feliciana 17, 28010 Madrid, España, 28010 Madrid   
1                                         4 Calle de Ramón y Cajal, 28801 Alcalá de Henares   
2                                                      14 Paseo de la Chopera, 28045 Madrid   
3                                           9 Carrer de Sorní #bajo derecha, 46004 València   
4                                                      14 Paseo de la Chopera, 28045 Madrid   

   longitude   latitude  \
0  -3.698552  40.433543   
1  -3.365515  40.482542   
2  -3.698443  40.392663   
3  -0.368432  39.470320   
4  -3.698443  40.392663   

                                                                                                                                       summary  \
0                     ¡Ven y disfruta de una mañana llena de historias, risas y diversión en nuestros cuenta cuentos, junto a Factoría Teatro!   
1  Talleres de podcast mensuales para niños. Nos reunimos el primer jueves de cada mes. Ven a probar un taller o apúntate a todos hasta julio.   
2                                                                                                                  Explorando y creando juntos   
3                Ven y aprende a dibujar letras de forma creativa en familia en nuestro taller de lettering, ¡te esperamos en la tienda RUBIO!   
4                                                                       Espacio de experimentación científica para niñas y niños de 2 a 8 años   

  is_online_event  \
0           False   
1           False   
2           False   
3           False   
4           False   

                                                      tickets_url  \
0  https://www.eventbrite.com/checkout-external?eid=1307028560609   
1  https://www.eventbrite.com/checkout-external?eid=1297237354849   
2  https://www.eventbrite.com/checkout-external?eid=1302039748939   
3  https://www.eventbrite.com/checkout-external?eid=1312720154319   
4  https://www.eventbrite.com/checkout-external?eid=1302072707519   

                                                                                                         

generando un nuevo mapa con ele dataset combinado, distinguiendo cada fonte de datos por color

In [29]:
# Generando el mapa a partir de las coordenadas con colores únicos por fuente

# Obtener las fuentes de datos únicas
unique_sources = combined_df['data_source'].unique()
num_sources = len(unique_sources)

# Define una lista de colores
available_colors = ['red', 'blue', 'green', 'purple', 'orange', 'darkred',
                    'beige', 'pink', 'black'
                    ]

# Mezcla los colores para asegurar una asignación algo aleatoria
random.shuffle(available_colors)
num_available_colors = len(available_colors)

# Crea un diccionario para asignar cada fuente única a un color
source_colors = {}
for i, source in enumerate(unique_sources):
    if i < num_available_colors:
        source_colors[source] = available_colors[i]
    else:
        # Manejar casos donde hay más fuentes que colores
        # Quizás quieras implementar una generación de color más sofisticada aquí
        # Para simplificar, volveremos a recorrer los colores, pero con una advertencia
        source_colors[source] = available_colors[i % num_available_colors]
        print(f"Warning: More data sources ({num_sources}) than available unique colors ({num_available_colors}). Colors may repeat.")

# Filtrar filas sin latitud o longitud
valid_events_df = combined_df.dropna(subset=['latitude', 'longitude', 'data_source'])

if not valid_events_df.empty:
    spain_latitude = 40.4637
    spain_longitude = -3.7492

    # Crear un mapa base centrado en España
    event_map = folium.Map(location=[spain_latitude, spain_longitude], zoom_start=7)

    # Iterar a través del DataFrame filtrado y agregar marcadores con color según data_source
    for _, row in valid_events_df.iterrows():
        data_source = row['data_source']
        marker_color = source_colors.get(data_source, 'gray')  # Predeterminado en gris si no se encuentra la fuente

        popup_html = f"""
        <strong>{row['name']}</strong><br>
        Fuente: <em>{data_source}</em><br>
        📍 <em>{row['venue_name']}</em><br>
        🗓 {row['start_date']} {row['start_time']} - {row['end_time']}<br>
        <a href="{row['url']}" target="_blank">Ver evento</a>
        """
        folium.Marker(
            location=[row['latitude'], row['longitude']],
            popup=folium.Popup(popup_html, max_width=300),
            tooltip=f"{row['name']} ({data_source})",
            icon=folium.Icon(color=marker_color)
        ).add_to(event_map)

    # Save como HTML:
    # event_map.save("event_map_unique_colored.html")
    
    # Para mostrar el mapa en el notebook:
    event_map
else:
    print("No events with valid latitude, longitude, or data_source to display on the map.")

In [30]:
event_map

In [31]:
# Crear la base de datos

DATABASE_FILE = 'events.db'
TABLE_NAME = 'all_events'
UNIQUE_ID_COLUMN = 'event_id'
LIST_COLUMNS_TO_CONVERT = ['tags']  # Convertir la columna tags de lista para formato string, la base de datos no accepta inserción del formato lista de python

def update_event_database(current_events_df):
    conn = sqlite3.connect(DATABASE_FILE)
    cursor = conn.cursor()

    # Obtener la lista de columnas del DataFrame, excluyendo la columna de ID única
    columns_list = [col for col in current_events_df.columns if col != UNIQUE_ID_COLUMN]
    columns_str = ', '.join(columns_list)
    placeholders = ', '.join(['?'] * len(columns_list))

    # Crear la tabla
    create_table_sql = f"CREATE TABLE IF NOT EXISTS {TABLE_NAME} ({UNIQUE_ID_COLUMN} TEXT PRIMARY KEY, {columns_str})"
    cursor.execute(create_table_sql)
    conn.commit()

    # Obtener datos unicos existentes de la base de datos
    cursor.execute(f"SELECT {UNIQUE_ID_COLUMN} FROM {TABLE_NAME}")
    existing_ids = {row[0] for row in cursor.fetchall()}

    new_events_to_insert = []
    for index, row in current_events_df.iterrows():
        unique_id = row[UNIQUE_ID_COLUMN]
        if unique_id not in existing_ids:
            data_to_insert = [unique_id]
            for col in columns_list:
                value = row[col]
                # Convertir objetos HTML a su representación de cadena
                if isinstance(value, HTML):
                    data_to_insert.append(str(value))
                # Convertir listas a una representación de string (por ejemplo, separadas por comas)
                elif isinstance(value, list):
                    data_to_insert.append(','.join(map(str, value)))
                else:
                    data_to_insert.append(value)
            new_events_to_insert.append(tuple(data_to_insert))  # Utilice tupla para ejecutar varios

    if new_events_to_insert:
        insert_placeholders = ', '.join(['?'] * (len(columns_list) + 1))
        insert_sql = f"INSERT INTO {TABLE_NAME} VALUES ({insert_placeholders})"
        cursor.executemany(insert_sql, new_events_to_insert)
        conn.commit()
        print(f"Inserted {len(new_events_to_insert)} new events into the database.")
    else:
        print("No new events found.")

    conn.close()

print("First few rows of combined_df:")
print(combined_df.head())

update_event_database(combined_df)

# Para cargar todos los eventos (incluidos los históricos) de la base de datos:
def load_all_events_from_db():
    conn = sqlite3.connect(DATABASE_FILE)
    all_events_df = pd.read_sql_query(f"SELECT * FROM {TABLE_NAME}", conn)
    conn.close()
    return all_events_df

all_events_df = load_all_events_from_db()
print("\nAll events loaded from the database:")
print(all_events_df.head())

First few rows of combined_df:
                                                                    name  \
0                                        Cuánto Cuento!  (de 0 a 6 años)   
1  Club Futuros Podcasters - Taller de podcast para niños de 6 a 12 años   
2                                     Jugar el arte en familia 3 DE MAYO   
3                Taller FAMILIAR de Lettering  ¡DIBUJAMOS EL ABECEDARIO!   
4               Investigactiva. Especial Energía y movimiento 18 DE MAYO   

                                                                                                                      url  \
0                                          https://www.eventbrite.es/e/entradas-cuanto-cuento-de-0-a-6-anos-1307028560609   
1  https://www.eventbrite.es/e/entradas-club-futuros-podcasters-taller-de-podcast-para-ninos-de-6-a-12-anos-1297237354849   
2                                   https://www.eventbrite.es/e/entradas-jugar-el-arte-en-familia-3-de-mayo-1302039748939   
3           

In [ ]:
# Consulta de prueba para verificar si la base de datos tiene los datos enviados.
pd.read_sql_query("SELECT * FROM all_events", sqlite3.connect('events.db'))
pd.read_sql_query("select count(*) from all_events", sqlite3.connect('events.db'))

count(*)
0       263

Conexión a la base de datos en Render y ejecución una consulta para recibir todos los datos, si es necesario, descargar todos los datos de la base de datos y luego guardar una copia de seguridad

In [ ]:
render_connection_string = os.getenv("RENDER_DB_URI")

# Creando motor SQLAlchemy
engine = create_engine(render_connection_string)

# Consulta SQL
sql_query = """
SELECT *
FROM all_events
"""

# Leer los datos en un Pandas DataFrame
try:
    df = pd.read_sql(sql_query, engine)
    print(df)
except Exception as e:
    print(f"Error: {e}")

engine.dispose()


           event_id  \
0      000000000003   
1      000000000004   
2      000000000006   
3      000000000009   
4      000000000010   
5      000000000012   
6      000000000014   
7      000000000015   
8      000000000017   
9      000000000019   
10     000000000020   
11     000000000022   
12     000000000023   
13     000000000025   
14     000000000027   
15     000000000029   
16     000000000030   
17     000000000032   
18     000000000034   
19     000000000035   
20     000000000037   
21     000000000039   
22     000000000040   
23     000000000042   
24     000000000044   
25     000000000045   
26     000000000047   
27     000000000049   
28     000000000050   
29     000000000052   
30     000000000053   
31     000000000055   
32     000000000057   
33     000000000058   
34     000000000060   
35     000000000001   
36     000000000002   
37     000000000005   
38     000000000007   
39     000000000011   
40     000000000013   
41     000000000016   
42     0000

guardando este df para generar la columna de ciudades

In [ ]:
df.to_csv('../data/raw/from_render_complete_db.csv', index=False)

In [138]:
df

event_id                                               name  \
0      000000000064                                          Pola Park   
1      000000000065                  Parque de Atracciones de Zaragoza   
2      000000000066                                   Zoo de Barcelona   
3      000000000067                                       Terra Mítica   
4      000000000068                                  Aquópolis Cartaya   
5      000000000069                              Aquarium de Barcelona   
6      000000000070                          Ferrari Land PortAventura   
7      000000000071                                           Aqualeón   
8      000000000072                                 Aqualand el Arenal   
9      000000000073                                       Warner Beach   
10     000000000074                                 Aqua Natura Murcia   
11     000000000075                           Mortenostrum Scream Park   
12     000000000076                                     Crocodile Park   
13     000000000077                                   Aquarock Menorca   
14     000000000078                            Aqua Park Costa Teguise   
15     000000000001                                     DinoPark Algar   
16     000000000002                                           Aqualava   
17     000000000003                                 Acuario de Sevilla   
18     000000000004                                     Oasis Wildlife   
19     000000000005                                        Loro Parque   
20     000000000006                                          Siam Park   
21     000000000007                                   Bioparc Valencia   
22     000000000008                                           Mundomar   
23     000000000009                                        Jungle Park   
24     000000000010                 Ciudad de las Artes y las Ciencias   
25     000000000011                                     Palma Aquarium   
26     000000000012                          Aquarium Costa de Almería   
27     000000000013                                       Oceanogràfic   
28     000000000014                              Acuario Poema del Mar   
29     000000000015                         Western Water Park Magaluf   
30     000000000016               Parque de la Naturaleza de Cabárceno   
31     000000000017                                  Puy du Fou Toledo   
32     000000000018                           Acuario de Gijón Bioparc   
33     000000000019                                Acuario de Zaragoza   
34     000000000020                                        Water World   
35     000000000021                             Aquadiver Platja d'Aro   
36     000000000022                               Aqualand Costa Adeje   
37     000000000023                                         Aqualandia   
38     000000000024                                Macabre Scream Park   
39     000000000025                                 Bioparc Fuengirola   
40     000000000026                                          Sendaviva   
41     000000000027                                  Aquarium Donostia   
42     000000000028                                   Dinópolis Teruel   
43     000000000029                                      Palmitos Park   
44     000000000030                                         Lacuniacha   
45     000000000031                               Marineland Catalunya   
46     000000000032                           Atlantis Aquarium Madrid   
47     000000000033                                         AquaTropic   
48     000000000034                                Aqualand Maspalomas   
49     000000000035                                      Zoo de Madrid   
50     000000000036                               Parque Warner Madrid   
51     000000000037                                        Isla Mágica   
52     000000000038                                       PortAventura   
53     00000000

-----------------------------

Función para manejar etiquetas redundantes y agruparlas por similitud

In [ ]:
def asignar_categoria(tags):
    categorias = set()
    lista_tags = [tag.strip() for tag in str(tags).split(',')]

    ocio_tags = {'Actividades','Arte','Audio','Bebé','Clase, formación o taller','Comedia en Barcelona','Comunicación','Evento','Comunidad','Crianza','Cuentacuentos','Cuentos','Familia','Familiar','Familias','Floral','Gratis','Grupo de bebés','Jovenes,Niños','Jovenes,Niños,Familias','Juego','Juegos','Lectura','Lettering','Libreria','Librería','Locutores','Madrid','Microfono','Montessori','Monólogo','Movimiento','Narración de cuentos','Narrador','Niños', 'Niños y familias','Niños y jóvenes','Niños,Familias','ocio','Podcast','Radio','Reunión','Taller','Taller familiar','affaires_de_famille','barcelona_comedy','certe_mathurin','colmena','eventos_infantiles','mathurin','me_mimo_gestando','un_nido_consciente'}
    viajes_tags = {}
    salud_tags = {'Comunidad','Conferencia','Conferencias','Estimulacion','Floral','Mama','Maternidad','Movimiento','Octubre','Silvestre','investigactiva'}
    educacion_tags = {'Clase, formación o taller','Comunicación','Consciência','Crianza','Curso','Educacion','Familia y educación','Jovenes,Niños','Jovenes,Niños,Familias','Lectura','Libreria','Librería','abecedario','dibujamos'}
    cine_tags = {'Concierto o actuación','Cuentacuentos','Cuentos','Humor','Teatro','cine'}

    encontrado_categoria = False
    for tag in lista_tags:
        if tag in ocio_tags:
            categorias.add('Ocio')
            encontrado_categoria = True
        elif tag in viajes_tags:
            categorias.add('Viajes')
            encontrado_categoria = True
        elif tag in salud_tags:
            categorias.add('Salud')
            encontrado_categoria = True
        elif tag in educacion_tags:
            categorias.add('Educación')
            encontrado_categoria = True
        elif tag in cine_tags:
            categorias.add('Cine')
            encontrado_categoria = True

    if not encontrado_categoria and lista_tags and lista_tags[0]:
        categorias.add('Otros')

    return ', '.join(sorted(list(categorias)))

# Aplicar la función al DataFrame
df['categoria'] = df['tags'].apply(asignar_categoria)

# Mostrar el resultado
print(df[['tags', 'categoria']].head(10))

   tags categoria
0  ocio      Ocio
1  ocio      Ocio
2  ocio      Ocio
3  ocio      Ocio
4  ocio      Ocio
5  ocio      Ocio
6  ocio      Ocio
7  ocio      Ocio
8  ocio      Ocio
9  ocio      Ocio


In [6]:
df.insert(16, 'categoria', df.pop('categoria'))

In [13]:
df_copy = df.copy()

In [35]:
# funcion para categorizar los eventos

import unicodedata
import pandas as pd
import numpy as np

def normalizar_texto(texto):
    texto = str(texto)
    texto = texto.lower()
    texto = unicodedata.normalize('NFKD', texto).encode('ascii', 'ignore').decode('utf-8')
    return texto

# Define las condiciones
conditions = [
    df_copy['name'].apply(normalizar_texto).str.contains(r'pato_teatro|teatro|obra|cine', regex=True),
    df_copy['name'].apply(normalizar_texto).str.contains('campamentos'),
    df_copy['name'].apply(normalizar_texto).str.contains('club'),
    df_copy['name'].apply(normalizar_texto).str.contains(r'clases|dojo|curso|ludoteca|taller|talleres', regex=True)
]

# Define los valores correspondientes a cada condición
choices = ['Cine', 'Viajes', 'Deportes', 'Educación']

# Aplica las condiciones y opciones, manteniendo el valor original si no se cumple ninguna
df_copy['categoria'] = np.select(conditions, choices, default=df_copy['categoria'])

# Para ver el resultado
print(df_copy[['name', 'categoria']].head())

                                name categoria
0                          Pola Park      Ocio
1  Parque de Atracciones de Zaragoza      Ocio
2                   Zoo de Barcelona      Ocio
3                       Terra Mítica      Ocio
4                  Aquópolis Cartaya      Ocio


In [139]:
df = df.drop(columns='categoria')

In [176]:
df.query('tags.str.contains("un_nido_consciente")')

event_id                                             name  \
692  1237774269159  Me Mimo Gestando, edición: "Un nido consciente"   

                                                   url start_time  start_date  \
692  https://www.eventbrite.es/e/me-mimo-gestando-e...      10:00  2025-05-24   

    end_time    end_date duration     venue_name  \
692    14:00  2025-05-24  4:00:00  ESPAI NERAIDA   

                                         venue_address  longitude    latitude  \
692  7 Camí del Transformador #B local A, 08394 San...  2.5094416  41.5760939   

                                               summary is_online_event  \
692  Solo con consciencia podremos abrirnos a la vi...           false   

                                           tickets_url  \
692  https://www.eventbrite.com/checkout-external?e...   

                                                  tags data_source image  \
692  Crianza,Familia y educación,Conferencia,Consci...  eventbrite   NaN   

    age_range  min_age  max_age  
692      None      NaN      NaN

In [141]:
df.to_csv('../data/raw/complete_data_db.csv')

In [40]:
# dataframe con categorias
df_copy.to_csv('../data/raw/complete_data_db.csv', index=False)

In [37]:
df_copy.columns

Index(['event_id', 'name', 'url', 'start_time', 'start_date', 'end_time',
       'end_date', 'duration', 'venue_name', 'venue_address', 'longitude',
       'latitude', 'summary', 'is_online_event', 'tickets_url', 'tags',
       'categoria', 'data_source', 'image', 'age_range', 'min_age', 'max_age'],
      dtype='object')

----------------------------

Actualizando la columna tags del DB

In [ ]:
RENDER_DB_URI = os.getenv("RENDER_DB_URI")

# Nombre de la tabla
TABLE_NAME = 'all_events'

# Columna que identifica de forma única cada evento
UNIQUE_ID_COLUMN = 'event_id'


try:
    # Crear el motor de SQLAlchemy
    engine = create_engine(RENDER_DB_URI)

    with engine.connect() as connection:
        for index, row in df_copy.iterrows():
            event_id = row.get(UNIQUE_ID_COLUMN)
            categoria = row.get('categoria')

            if event_id is not None and categoria is not None:
                # Intentar actualizar la fila existente basada en el UNIQUE_ID_COLUMN
                update_query = text(f"""
                    UPDATE {TABLE_NAME}
                    SET tags = :categoria
                    WHERE {UNIQUE_ID_COLUMN} = :event_id
                """)
                connection.execute(update_query, {"categoria": categoria, "event_id": event_id})
            else:
                print(f"Advertencia: No se pudo actualizar la fila con índice {index} porque faltan '{UNIQUE_ID_COLUMN}' o 'categoria'.")

        # Confirmar los cambios
        connection.commit()

    print(f"Columna 'categoria' actualizada en la columna 'tags' de la tabla '{TABLE_NAME}'.")

except Exception as e:
    print(f"Ocurrió un error al conectar o actualizar la base de datos: {e}")
finally:
    if 'engine' in locals() and engine is not None:
        engine.dispose() # Libera la conexión del pool

Columna 'categoria' actualizada en la columna 'tags' de la tabla 'all_events'.
